In [1]:
# make sure jupyter path is correct for loading local moudules
import sys
# path to steric_simulator module relative to notebook
sys.path.append("../../../")
import copy
from steric_free_simulator import ReactionNetwork, VectorizedRxnNet, VecSim, Optimizer, EquilibriumSolver

EnergyExplorer Module is not available. Check Rosetta installation. <ipykernel.iostream.OutStream object at 0x7f9a59abb080>


In [2]:
base_input = '../../input_files/ap2.pwr'
rn = ReactionNetwork(base_input, one_step=True)
rn.resolve_tree()

['A']
['M']
['B']
['S']
-----
{'A'}
{'A'}
set()
-----
{'A'}
{'M'}
{'A'}
False
Allowed edges: 
('A', 'B')
Allowed edges: 
('A', 'M')
Connected Nodes:  ['A', 'M']
Connected Edges:  [('A', 'M')]
Allowed edges: 
('A', 'S')
Allowed edges: 
('B', 'M')
Allowed edges: 
('M', 'S')
New node added--1
['A', 'M']
{('A', 'B'): [None, None, 1, tensor([-10000.], dtype=torch.float64)], ('A', 'M'): [None, None, 1, tensor([-10000.], dtype=torch.float64)], ('A', 'S'): [None, None, 1, tensor([-10000.], dtype=torch.float64)], ('B', 'M'): [None, None, 1, tensor([-10000.], dtype=torch.float64)], ('M', 'S'): [None, None, 1, tensor([-10000.], dtype=torch.float64)]}
New node added--2
[0, 1, 2, 3, 4]
-----
{'A'}
{'B'}
{'A'}
False
Allowed edges: 
('A', 'B')
Connected Nodes:  ['A', 'B']
Connected Edges:  [('A', 'B')]
Allowed edges: 
('A', 'M')
Allowed edges: 
('A', 'S')
Allowed edges: 
('B', 'M')
Allowed edges: 
('M', 'S')
New node added--1
['A', 'B']
{('A', 'B'): [None, None, 1, tensor([-10000.], dtype=torch.float

{('A', 'B'): [None, None, 1, tensor([-10000.], dtype=torch.float64)], ('A', 'M'): [None, None, 1, tensor([-10000.], dtype=torch.float64)], ('A', 'S'): [None, None, 1, tensor([-10000.], dtype=torch.float64)], ('B', 'M'): [None, None, 1, tensor([-10000.], dtype=torch.float64)], ('M', 'S'): [None, None, 1, tensor([-10000.], dtype=torch.float64)]}
-----
{'B', 'A', 'S'}
{'B'}
{'A', 'S'}
-----
{'B', 'A', 'S'}
{'S'}
{'B', 'A'}
-----
{'B', 'A', 'S'}
{'A', 'M'}
{'B', 'S'}
-----
{'B', 'A', 'S'}
{'A', 'B'}
{'S'}
-----
{'B', 'A', 'S'}
{'A', 'S'}
{'B'}
-----
{'B', 'A', 'S'}
{'B', 'M'}
{'A', 'S'}
-----
{'B', 'A', 'S'}
{'M', 'S'}
{'B', 'A'}
-----
{'B', 'A', 'S'}
{'A', 'B', 'M'}
{'S'}
-----
{'B', 'A', 'S'}
{'A', 'M', 'S'}
{'B'}
-----
{'B', 'A', 'S'}
{'B', 'A', 'S'}
set()
-----
{'B', 'A', 'S'}
{'B', 'M', 'S'}
{'A'}
-----
{'B', 'A', 'S'}
{'B', 'A', 'M', 'S'}
set()
Allowed edges: 
('A', 'B')
Allowed edges: 
('A', 'M')
Allowed edges: 
('A', 'S')
Allowed edges: 
('B', 'M')
Allowed edges: 
('M', 'S')
-----


In [3]:
uid_dict = {}
sys.path.append("../../")
import numpy as np
from reaction_network import gtostr
for n in rn.network.nodes():
    #print(n)
    #print(rn.network.nodes()[n])
    for k,v in rn.network[n].items():
        uid = v['uid']
        r1 = set(gtostr(rn.network.nodes[n]['struct']))
        p = set(gtostr(rn.network.nodes[k]['struct']))
        r2 = p-r1
        reactants = (r1,r2)
        uid_dict[(n,k)] = uid

print(uid_dict)

{(0, 4): 0, (0, 5): 1, (0, 6): 2, (0, 9): 17, (0, 10): 18, (0, 13): 20, (1, 4): 0, (1, 7): 3, (1, 8): 4, (1, 9): 5, (1, 10): 6, (1, 13): 19, (2, 5): 1, (2, 7): 3, (2, 9): 7, (2, 11): 8, (2, 12): 9, (2, 13): 10, (3, 6): 2, (3, 8): 4, (3, 10): 11, (3, 11): 12, (3, 12): 13, (3, 13): 14, (4, 9): 7, (4, 10): 11, (5, 9): 5, (5, 11): 12, (5, 13): 15, (6, 10): 6, (6, 11): 8, (6, 13): 16, (7, 12): 13, (7, 13): 16, (7, 9): 17, (8, 12): 9, (8, 13): 15, (8, 10): 18, (9, 13): 14, (10, 13): 10, (11, 13): 19, (12, 13): 20}


In [4]:
sys.path.append("../../")
import numpy as np
from reaction_network import gtostr
from torch import DoubleTensor as Tensor
import torch

node_map = {}
for node in rn.network.nodes():
    node_map[gtostr(rn.network.nodes[node]['struct'])] = node
def get_max_edge(vec_rn,n,node_map):
    """
    Calculates the max rate (k_on) for a given node
    To find out the maximum flow path to the final complex starting from the current node.
    
    Can also calculate the total rate of consumption of a node by summing up all rates. 
    Can tell which component is used quickly.
    """
    try:
        edges = rn.network.out_edges(n)
        #Loop over all edges
        #Get attributes
        if len(edges)==0:
            return(False)
        kon_max = -1
        next_node = -1
        
        kon_sum = 0
        for edge in edges:
            data = rn.network.get_edge_data(edge[0],edge[1])
            #print(data)
            #Get uid
            uid = data['uid']
            #Get updated kon
            temp_kon = vec_rn.kon[uid]
            kon_sum+=temp_kon
            
            if temp_kon > kon_max:
                kon_max = temp_kon
                next_node=edge[1]
        return(kon_max,next_node,kon_sum)
    except Exception as err:
        raise(err)
def get_node_flux(vec_rn,n):
    total_flux_outedges = 0
    total_flux_inedges = 0
    #Go over all the out edges
    edges_out = rn.network.out_edges(n)
    if len(edges_out)>0:

        for edge in edges_out:
            data = rn.network.get_edge_data(edge[0],edge[1])
            #print(data)
            #Get uid
            uid = data['uid']

            #Get updated kon
            temp_kon = vec_rn.kon[uid]

            #Calculate k_off also
            std_c = Tensor([1.])
            l_kon = torch.log(temp_kon)
            l_koff = (vec_rn.rxn_score_vec[uid] * 1. / (vec_rn._R * vec_rn._T)) + l_kon + torch.log(std_c)
            koff = torch.exp(l_koff)

            #Getting conc. of reactants and products
            #Get product
            prod = gtostr(rn.network.nodes[edge[1]]['struct']) 
            #Get other reactant
            react = "".join(sorted(list(set(prod) - set(gtostr(rn.network.nodes[edge[0]]['struct']) ))))

            #Net flux from this edge = Generation - consumption
            edge_flux = koff*vec_rn.copies_vec[edge[1]] - temp_kon*(vec_rn.copies_vec[edge[0]])*(vec_rn.copies_vec[node_map[react]])
            #edge_flux = koff*vec_rn.copies_vec[edge[1]] 

#             print("Reaction: ", gtostr(rn.network.nodes[edge[0]]['struct']), "+",react," -> ",prod)
#             print("Net flux: ",edge_flux)
#             print("kon : ",temp_kon)
#             print("koff: ",koff)
#             print("Reaction data OUTWARD: ")
#             print(data)

            total_flux_outedges+=edge_flux
    
    #Now go over all the in edges
    edges_in = rn.network.in_edges(n)
    react_list = []
    if len(edges_in) > 0:
        for edge in edges_in:
            if edge[0] in react_list:
                continue
            data = rn.network.get_edge_data(edge[0],edge[1])
            uid = data['uid']


            #Get generation rates; which would be kon
            temp_kon = vec_rn.kon[uid]

            #Get consumption rates; which is k_off
            std_c = Tensor([1.])
            l_kon = torch.log(temp_kon)
            l_koff = (vec_rn.rxn_score_vec[uid] * 1. / (vec_rn._R * vec_rn._T)) + l_kon + torch.log(std_c)
            koff = torch.exp(l_koff)

            #Get conc. of reactants and products
            prod = gtostr(rn.network.nodes[edge[1]]['struct'])
            #Get other reactant
            react = "".join(sorted(list(set(prod) - set(gtostr(rn.network.nodes[edge[0]]['struct']) ))))
            react_list.append(node_map[react])
            #Net flux from this edge = Generation - consumption
            edge_flux_in = temp_kon*(vec_rn.copies_vec[edge[0]])*(vec_rn.copies_vec[node_map[react]])- koff*vec_rn.copies_vec[edge[1]]
            #edge_flux_in = koff*vec_rn.copies_vec[edge[1]]
            


#             print("Reaction: ", prod ," -> ",gtostr(rn.network.nodes[edge[0]]['struct']), "+",react)
#             print("Net flux: ",edge_flux_in)
#             print("kon : ",temp_kon)
#             print("koff: ",koff)
#             print("Raction data INWARD: ")
#             print(data)

            total_flux_inedges+=edge_flux_in
    net_node_flux = total_flux_outedges + total_flux_inedges
    
    return(net_node_flux)

def do_flux_analysis(vec_rn,node_map):
    pathway = []
    kon_sumarray = []
    total_con_rate = {}
    net_flux = {}
    for n in rn.network.nodes():

        n_str = gtostr(rn.network.nodes[n]['struct']) 

        paths = [n_str]
        kon_sum = 0
        temp_node = n
        max_edge = True
        consumption_rate = 0
        if n < len(rn.network.nodes()):#num_monomers:
    #         print("Current node: ")
    #         print(n_str)
            while max_edge:
                max_edge = get_max_edge(vec_rn,temp_node,node_map)
                if max_edge:
                    total_con_rate[gtostr(rn.network.nodes[temp_node]['struct'])] = max_edge[2]
                    temp_node = max_edge[1]
                    kon_sum += max_edge[0].item()


    #                 print("Next node: ")
    #                 print(temp_node)

                    paths.append(gtostr(rn.network.nodes[temp_node]['struct']))
                else:
                    break
            pathway.append(paths)
            kon_sumarray.append(kon_sum)
            paths=[]
            
        net_flux[gtostr(rn.network.nodes[n]['struct'])] = get_node_flux(vec_rn,n)

    #print(pathway)
    #print(kon_sumarray)
    
    return(total_con_rate,net_flux)

In [ ]:
## Changing Initial Conditions
import networkx as nx
#Changin k_on
kon_list = [1.0,10.0]# uM-1 s-1

final_yield = {kon : [] for kon in kon_list}
optimized_rates = {kon : [] for kon in kon_list}
observables = {kon : dict() for kon in kon_list} 
flux_data = {kon : [] for kon in kon_list}
cons_data = {kon : [] for kon in kon_list}
final_copies = {kon : [] for kon in kon_list}

for new_kon in kon_list:

    nx.set_edge_attributes(rn.network,new_kon,'k_on')
    
    
    vec_rn = VectorizedRxnNet(rn, dev='cpu')
    vec_rn.reset(reset_params=True)
    
    ### Start Optimization
    print("Running Optimization with the following on rates: ")
    print(vec_rn.kon)
    optim = Optimizer(reaction_network=vec_rn,
                      sim_runtime=1,
                      optim_iterations=10000,
                      learning_rate=new_kon/1000,
                      device='cpu')
    optim.rn.update_reaction_net(rn)
    optim.optimize()
    
    final_yield[new_kon] = optim.yield_per_iter
    optimized_rates[new_kon] = vec_rn.kon
    
    ###Run simulation with optimized parameters
    print("Running simulation with optimized parameters")
    optim_rn = optim.rn
    sim_times = [1,2,10]
    for i, runtime in enumerate(sim_times):
        optim_rn.reset()
        sim = VecSim(optim_rn, runtime, device='cpu')
        y = sim.simulate()
        
        observables[new_kon][runtime] = (sim.steps.copy(),sim.observables.copy())
        print("Length of observables: ", len(sim.observables[0][1]))
    
    ##Calculate the net flux in across each node/species
    print("Doing flux analysis")
    cons_rate,flux = do_flux_analysis(vec_rn,node_map)
    
    flux_data[new_kon].append(flux)
    cons_data[new_kon].append(cons_rate)
    final_copies[new_kon].append(vec_rn.copies_vec)
    
        
    

A
M
B
S
AM
AB
AS
BM
MS
ABM
AMS
ABS
BMS
ABMS
Running Optimization with the following on rates: 
Parameter containing:
tensor([1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1.], dtype=torch.float64, requires_grad=True)
Using CPU
Reaction Parameters before optimization: 
[Parameter containing:
tensor([1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1., 1.,
        1., 1., 1.], dtype=torch.float64, requires_grad=True)]
Using CPU
Next time:  tensor(1.4692, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 0 was 47.1%
current params: tensor([0.9990, 1.0010, 1.0010, 0.9990, 0.9990, 0.9990, 0.9990, 1.0010, 0.9990,
        0.9990, 1.0010, 1.0010, 0.9990, 0.9990, 1.0010, 1.0010, 1.0010, 0.9990,
        0.9990, 0.9990, 1.0010], dtype=torch.float64)
Using CPU
Next time:  tensor(1.4687, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 1 was 47.2%
current params: tensor([0.9980, 1.0004, 1.0004, 0.9985, 0.9

Next time:  tensor(1.1370, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 23 was 47.0%
current params: tensor([0.9769, 0.9895, 0.9895, 0.9909, 0.9909, 0.9807, 0.9807, 1.0218, 0.9765,
        0.9765, 1.0235, 1.0218, 0.9765, 0.9765, 1.0235, 1.0223, 1.0223, 0.9800,
        0.9800, 1.0083, 1.0063], dtype=torch.float64)
Using CPU
Next time:  tensor(1.1335, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 24 was 47.0%
current params: tensor([0.9760, 0.9895, 0.9895, 0.9909, 0.9909, 0.9801, 0.9801, 1.0223, 0.9756,
        0.9756, 1.0244, 1.0223, 0.9756, 0.9756, 1.0244, 1.0230, 1.0230, 0.9794,
        0.9794, 1.0090, 1.0069], dtype=torch.float64)
Using CPU
Next time:  tensor(1.1301, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 25 was 47.1%
current params: tensor([0.9752, 0.9894, 0.9894, 0.9910, 0.9910, 0.9794, 0.9794, 1.0228, 0.9747,
        0.9747, 1.0253, 1.0228, 0.9747, 0.9747, 1.0253, 1.0236, 1.0236, 0.9787,
        0.9787, 1.00

current params: tensor([0.9572, 0.9951, 0.9951, 0.9980, 0.9980, 0.9646, 0.9646, 1.0303, 0.9542,
        0.9542, 1.0453, 1.0303, 0.9542, 0.9542, 1.0453, 1.0358, 1.0358, 0.9644,
        0.9644, 1.0281, 1.0257], dtype=torch.float64)
Using CPU
Next time:  tensor(1.0601, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 49 was 47.6%
current params: tensor([0.9564, 0.9955, 0.9955, 0.9985, 0.9985, 0.9640, 0.9640, 1.0305, 0.9533,
        0.9533, 1.0462, 1.0305, 0.9533, 0.9533, 1.0462, 1.0363, 1.0363, 0.9638,
        0.9638, 1.0289, 1.0266], dtype=torch.float64)
Using CPU
Next time:  tensor(1.0574, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 50 was 47.7%
current params: tensor([0.9556, 0.9959, 0.9959, 0.9989, 0.9989, 0.9633, 0.9633, 1.0308, 0.9524,
        0.9524, 1.0471, 1.0308, 0.9524, 0.9524, 1.0471, 1.0368, 1.0368, 0.9631,
        0.9631, 1.0298, 1.0275], dtype=torch.float64)
Using CPU
Next time:  tensor(1.0547, dtype=torch.float64, grad_fn=<AddBack

Next time:  tensor(1.0051, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 73 was 48.3%
current params: tensor([0.9364, 1.0063, 1.0063, 1.0103, 1.0103, 0.9469, 0.9469, 1.0368, 0.9311,
        0.9310, 1.0673, 1.0368, 0.9311, 0.9310, 1.0673, 1.0496, 1.0496, 0.9476,
        0.9476, 1.0501, 1.0482], dtype=torch.float64)
Using CPU
Next time:  tensor(1.0024, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 74 was 48.3%
current params: tensor([0.9356, 1.0068, 1.0068, 1.0108, 1.0108, 0.9462, 0.9462, 1.0371, 0.9301,
        0.9301, 1.0682, 1.0371, 0.9301, 0.9301, 1.0682, 1.0501, 1.0501, 0.9469,
        0.9469, 1.0510, 1.0492], dtype=torch.float64)
Using CPU
Next time:  tensor(1.0074, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 75 was 48.4%
current params: tensor([0.9347, 1.0073, 1.0073, 1.0114, 1.0114, 0.9454, 0.9454, 1.0373, 0.9292,
        0.9291, 1.0691, 1.0373, 0.9292, 0.9291, 1.0691, 1.0507, 1.0507, 0.9461,
        0.9461, 1.05

Next time:  tensor(2.1403, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 97 was 52.8%
current params: tensor([0.9123, 1.0136, 1.0136, 1.0182, 1.0182, 0.9278, 0.9278, 1.0507, 0.9041,
        0.9041, 1.0889, 1.0507, 0.9041, 0.9041, 1.0889, 1.0703, 1.0703, 0.9296,
        0.9296, 1.0747, 1.0738], dtype=torch.float64)
Using CPU
Next time:  tensor(2.2023, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 98 was 53.0%
current params: tensor([0.9111, 1.0136, 1.0136, 1.0183, 1.0183, 0.9270, 0.9270, 1.0516, 0.9029,
        0.9029, 1.0898, 1.0516, 0.9029, 0.9029, 1.0898, 1.0714, 1.0714, 0.9288,
        0.9288, 1.0759, 1.0749], dtype=torch.float64)
Using CPU
Next time:  tensor(2.2664, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 99 was 53.1%
current params: tensor([0.9100, 1.0136, 1.0136, 1.0183, 1.0183, 0.9261, 0.9261, 1.0525, 0.9016,
        0.9016, 1.0908, 1.0525, 0.9016, 0.9016, 1.0908, 1.0726, 1.0726, 0.9280,
        0.9280, 1.07

...

Next time:  tensor(1.3026, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 6165 was 71.7%
current params: tensor([ 9.4712, 11.4080, 11.2173, 11.4394, 11.2060, 23.8049, 21.1956, 28.8064,
         8.1783,  8.1749, 29.4923, 28.8736,  8.1735,  8.1742, 27.4552,  7.2290,
         7.2255, 24.6796, 21.4159, 12.1045, 11.9434], dtype=torch.float64)
Using CPU
Next time:  tensor(1.1038, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 6166 was 70.4%
current params: tensor([ 9.4714, 11.4081, 11.2173, 11.4396, 11.2060, 23.8054, 21.1959, 28.8075,
         8.1781,  8.1744, 29.4943, 28.8747,  8.1740,  8.1740, 27.4561,  7.2289,
         7.2255, 24.6811, 21.4163, 12.1046, 11.9435], dtype=torch.float64)
Using CPU
Next time:  tensor(1.1038, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 6167 was 70.4%
current params: tensor([ 9.4718, 11.4081, 11.2173, 11.4397, 11.2060, 23.8060, 21.1963, 28.8088,
         8.1777,  8.1739, 29.4963, 28.8759,  8.1745,

Next time:  tensor(1.1031, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 6188 was 70.4%
current params: tensor([ 9.4793, 11.4097, 11.2168, 11.4418, 11.2063, 23.8170, 21.2035, 28.8344,
         8.1781,  8.1855, 29.5391, 28.9002,  8.1750,  8.1769, 27.4754,  7.2279,
         7.2245, 24.7153, 21.4257, 12.1075, 11.9446], dtype=torch.float64)
Using CPU
Next time:  tensor(1.1032, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 6189 was 70.4%
current params: tensor([ 9.4803, 11.4096, 11.2167, 11.4418, 11.2063, 23.8176, 21.2039, 28.8358,
         8.1785,  8.1852, 29.5412, 28.9014,  8.1748,  8.1768, 27.4764,  7.2280,
         7.2246, 24.7171, 21.4262, 12.1076, 11.9446], dtype=torch.float64)
Using CPU
Next time:  tensor(1.3020, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 6190 was 71.7%
current params: tensor([ 9.4809, 11.4096, 11.2167, 11.4419, 11.2063, 23.8181, 21.2042, 28.8370,
         8.1789,  8.1850, 29.5432, 28.9026,  8.1746,

Next time:  tensor(1.1034, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 6211 was 70.4%
current params: tensor([ 9.4842, 11.4124, 11.2169, 11.4449, 11.2071, 23.8288, 21.2113, 28.8623,
         8.1784,  8.1779, 29.5863, 28.9266,  8.1763,  8.1731, 27.4957,  7.2262,
         7.2229, 24.7503, 21.4355, 12.1103, 11.9460], dtype=torch.float64)
Using CPU
Next time:  tensor(1.1035, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 6212 was 70.4%
current params: tensor([ 9.4846, 11.4124, 11.2169, 11.4450, 11.2072, 23.8293, 21.2117, 28.8635,
         8.1781,  8.1774, 29.5883, 28.9277,  8.1763,  8.1728, 27.4966,  7.2261,
         7.2229, 24.7518, 21.4360, 12.1104, 11.9460], dtype=torch.float64)
Using CPU
Next time:  tensor(1.3011, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 6213 was 71.7%
current params: tensor([ 9.4847, 11.4126, 11.2169, 11.4452, 11.2072, 23.8298, 21.2120, 28.8647,
         8.1778,  8.1770, 29.5904, 28.9289,  8.1763,

Next time:  tensor(1.1029, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 6234 was 70.4%
current params: tensor([ 9.4887, 11.4152, 11.2171, 11.4482, 11.2080, 23.8407, 21.2192, 28.8903,
         8.1781,  8.1858, 29.6339, 28.9532,  8.1736,  8.1769, 27.5161,  7.2243,
         7.2212, 24.7851, 21.4454, 12.1132, 11.9471], dtype=torch.float64)
Using CPU
Next time:  tensor(1.1029, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 6235 was 70.4%
current params: tensor([ 9.4894, 11.4152, 11.2170, 11.4482, 11.2080, 23.8413, 21.2196, 28.8916,
         8.1787,  8.1860, 29.6360, 28.9544,  8.1733,  8.1768, 27.5170,  7.2243,
         7.2212, 24.7868, 21.4459, 12.1133, 11.9471], dtype=torch.float64)
Using CPU
Next time:  tensor(1.1029, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 6236 was 70.4%
current params: tensor([ 9.4901, 11.4152, 11.2170, 11.4482, 11.2080, 23.8419, 21.2200, 28.8930,
         8.1791,  8.1861, 29.6381, 28.9557,  8.1731,

Next time:  tensor(1.1030, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 6257 was 70.4%
current params: tensor([ 9.4964, 11.4173, 11.2168, 11.4508, 11.2085, 23.8531, 21.2274, 28.9192,
         8.1787,  8.1815, 29.6821, 28.9805,  8.1758,  8.1748, 27.5369,  7.2230,
         7.2200, 24.8218, 21.4556, 12.1162, 11.9484], dtype=torch.float64)
Using CPU
Next time:  tensor(1.1030, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 6258 was 70.4%
current params: tensor([ 9.4970, 11.4173, 11.2168, 11.4509, 11.2085, 23.8536, 21.2278, 28.9205,
         8.1783,  8.1810, 29.6842, 28.9818,  8.1757,  8.1753, 27.5378,  7.2230,
         7.2200, 24.8235, 21.4560, 12.1164, 11.9484], dtype=torch.float64)
Using CPU
Next time:  tensor(1.1031, dtype=torch.float64, grad_fn=<AddBackward0>)
yield on sim iteration 6259 was 70.4%
current params: tensor([ 9.4978, 11.4173, 11.2167, 11.4509, 11.2085, 23.8542, 21.2281, 28.9219,
         8.1779,  8.1804, 29.6863, 28.9830,  8.1755,

In [ ]:
##Plotting yield for each optimized rates
from matplotlib import pyplot as plt
%matplotlib inline
fig, ax = plt.subplots(1, len(kon_list))
i= 0
for kon,val in final_yield.items():
    ax[i].plot(val)
    ax[i].set_title("Initial kon = " + str(kon))
    i+=1
    

txt = fig.suptitle("Yield after optimization")
fig.set_size_inches(24, 6)
fig.tight_layout()
plt.show()

In [ ]:
times = 3
fig,ax = plt.subplots(len(kon_list),times)
i=0
nodes_list = ['A','B','M','S','AB','AM','AS','ABM','AMS','ABS','BSM','ABMS']
for kon,runtimes in observables.items():
    for time,val in runtimes.items():
        #print(time)
        for key in val[1].keys():
            if val[1][key][0] in nodes_list:
                row = int(i/times)
                col = i%times
                #print(val[1][key][1][:5])
                #print(len(val[1][key][1]))
                ax[row,col].plot(val[0],val[1][key][1],label=val[1][key][0])
        ax[row,col].set_title("runtime: " + str(time) + " seconds")
        i+=1
lgnd = plt.legend(loc='best')
fig.set_size_inches(18, 8)
fig.tight_layout()
plt.show()

In [ ]:
for kon,flux in flux_data.items():
    print("-----------------------")
    print("Starting on rate: ", kon)
    print("Final copies: ", final_copies[kon])
    print("Optimzied parameters: ", optimized_rates[kon])
    
    print("Flux: ")
    for k,v in sorted(flux[0].items(),key=lambda x : x[1]):
        print(k," : ", v)